In [1]:
import json
import requests

/home/stefan/.venvs/dev/lib/python3.11/site-packages/requests/__init__.py:102: RequestsDependencyWarning: urllib3 (1.26.7) or chardet (5.2.0)/charset_normalizer (2.0.7) doesn't match a supported version!
  warnings.warn("urllib3 ({}) or chardet ({})/charset_normalizer ({}) doesn't match a supported "


In [2]:
base_url = "https://raw.githubusercontent.com/UniversalDependencies/UD_German-GSD"
commit = "e5f625a0d438cb8b31d3d640a3edd21ff16359a0"

In [3]:
splits = ["train", "dev", "test"]

In [4]:
f_out = open(f"UD_German-GSD_{commit[:7]}.jsonl", "wt")

for split in splits:
    current_url = f"{base_url}/{commit}/de_gsd-ud-{split}.conllu"
    r = requests.get(current_url)

    if not r:
        print(f"Could not retrieve data for split {split}")
    
    content = r.text
    
    current_sent_id = None
    current_text = None
    
    for line in content.split("\n"):
        if line.startswith("#"):
            if line.startswith("# sent_id = "):
                current_sent_id = line.split(" = ")[-1]
            elif line.startswith("# text = "):
                current_text = line.split(" = ")[-1]
        else:
            if current_sent_id and current_text:
                f_out.write(json.dumps({
                    "sent_id": current_sent_id,
                    "text": current_text,
                    "split": split
                }) + "\n")
                
                current_sent_id = None
                current_text = None
    
f_out.close()